In [1]:
from pathlib import Path
query='O93430' #UniPortKB ID
mer=5 #Total number of chains
cwd=Path("glra1_danre") #This directory must exist
cwd.mkdir(exist_ok=True)
exclude=None #[List of PDB IDs] 
#If you already know some structures you want to exclude provide them as a list. 

In [2]:
from pdbParser.prep_ensemble import PDBInfo
info=PDBInfo(query,mer,exclude=exclude) #Add the exclude argument to the end.

In [3]:
info.query #UniPort ID used to initialize this class
#and it is also used for the output names.
print(info.mer) # Total number of chains
print(info.result) #Contains the information from the 3D structures table.
print(info.refseq) #Contains the reference sequence. 

5
{'3JAD': [1, [['A', 'B', 'C', 'D', 'E']]], '3JAE': [1, [['A', 'B', 'C', 'D', 'E']]], '3JAF': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLO': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLP': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLQ': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLR': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLS': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLT': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLU': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLV': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLW': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLX': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLY': [1, [['A', 'B', 'C', 'D', 'E']]], '6PLZ': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM0': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM1': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM2': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM3': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM4': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM5': [1, [['A', 'B', 'C', 'D', 'E']]], '6PM6': [1, [['A', 'B', 'C', 'D', 'E']]], '6PXD': [1, [['A', 'B', 'C', 'D', 'E']]], '6UBS': [1, [['A', 'B', 'C', 'D

In [16]:
info.downloadPDB(cwd)
info.process_pdbs(cwd)

In [8]:
clustalopath="/home/ozyo/.local/bin/clustalo-1.2.4-Ubuntu-x86_64"
r=info.msa_missing_domain(cwd,clustalopath,profile="profile_aln.txt")

In [17]:
info.broken
info.get_core_mis(cwd)

In [30]:
from MDAnalysis import Universe
from MDAnalysis.analysis import align
import pandas as pd

def align_get_rmsd(ref_id:str,cwd:Path):
    ref = Universe(f"{cwd}/clean_pdbs/correct_{ref_id}.pdb")
    data = {"pdb_name":[],"rmsd":[],"universes":[]}
    for pdb in info.coremer:
        if pdb in info.broken:
            continue
        u=Universe(f"{cwd}/clean_pdbs/correct_{pdb}")
        a = align.AlignTraj(u,ref,in_memory=True)
        a.run()
        data["pdb_name"].append(pdb)
        data["universes"].append(u)
        data["rmsd"].append(a.results.rmsd[0])
    data=pd.DataFrame(data)
    print(data[data.rmsd > 5])
    return data

rmsd=align_get_rmsd('3JAD_1',cwd)

/home/ozyo/.local/lib/python3.9/site-packages/MDAnalysis/coordinates/base.py:892: UserWarning: Reader has no dt information, set to 1.0 ps
  warnings.warn("Reader has no dt information, set to 1.0 ps")


Empty DataFrame
Columns: [pdb_name, rmsd, universes]
Index: []


As you can see in the above analysis we have quite a few PDB files that show a high RMSD difference to the reference. They are outliers and most of the time you have to examine what's wrong manually in each file and either discard or repair them. GLIC has 5 subunits arranged in counter-clockwise order, usually, however, the PDB files above do not contain chains in the counter-clockwise order and their order needs to be changed.

In [31]:
from pdbParser import chorder
from importlib import reload
reload(chorder)
b=rmsd[rmsd.rmsd>5].pdb_name.to_list()
forced ={k:['A','E','D','C','B'] for k in b}
chorder.forceorder({k:v for k,v in info.coremer.items() if k not in info.broken},cwd/"clean_pdbs",tag="correct_", alph=False,forordict=forced)
rmsd = align_get_rmsd('3JAD_1',cwd)

for _,row in rmsd.iterrows():
    row['universes'].select_atoms("all").write(f"{cwd}/clean_pdbs/correct_{row['pdb_name']}")

/home/ozyo/.local/lib/python3.9/site-packages/MDAnalysis/coordinates/base.py:892: UserWarning: Reader has no dt information, set to 1.0 ps
  warnings.warn("Reader has no dt information, set to 1.0 ps")


Empty DataFrame
Columns: [pdb_name, rmsd, universes]
Index: []


/home/ozyo/.local/lib/python3.9/site-packages/MDAnalysis/coordinates/PDB.py:747: UserWarning: Unit cell dimensions not found. CRYST1 record set to unitary values.
  warnings.warn("Unit cell dimensions not found. "


In [34]:
%%bash
touch glra1_danre/GLYR_ensemble.pdb
for pdb in `ls -1 glra1_danre/clean_pdbs/correct*pdb`
do
echo "MODEL" >> glra1_danre/GLYR_ensemble.pdb
cat $pdb >> glra1_danre/GLYR_ensemble.pdb
echo "END" >> glra1_danre/GLYR_ensemble.pdb
done

In [35]:
info.core_show(cwd)